In [1]:
import tech_lib as tech
import binance_api as binance
%load_ext autoreload
%autoreload 2
import itertools
import pandas as pd
import numpy as np
import os
from datetime import datetime
import torch
print(f'Cuda available: {torch.cuda.is_available()}')
print(f'Cuda version: {torch.version.cuda}')
print(f'Cuda device name: {torch.cuda.get_device_name(0)}')

Cuda available: True
Cuda version: 12.6
Cuda device name: NVIDIA GeForce RTX 4060


In [2]:
api_key = 'lmxX1ymc6vGTQYkgUR194NeUxrhZQXM2xnf0rvjtQV4XxgP9xS9rawF6CvQRO2pw'
api_secret = 'rNFCb6OYjktZ1O6yfpNy1EItYJGwOMe8rtW8salpdXDHaNQGdxJDwpqgXrysxjN7'

ticker = 'BTCUSDT'
interval = '1m'
start_date = (2024, 6, 15, 0, 0, 0)
end_date = (2025, 1, 15, 0, 0, 0)

start_date_str = datetime(*start_date).strftime('%Y%m%d')
end_date_str = datetime(*end_date).strftime('%Y%m%d')
dataset_path = os.getcwd()+f'\\dataset\\{ticker}-{interval}-{start_date_str}-{end_date_str}.csv'

if os.path.exists(dataset_path):
    dataset = pd.read_csv(dataset_path, index_col='Open Time')
else:
    dataset = binance.historical_data(
        api_key,
        api_secret,
        ticker,
        interval,
        start_date,
        end_date
    )
    dataset = dataset.drop(['Ignore', 'Close Time'], axis=1)

dataset.to_csv(dataset_path)

In [3]:
#Calcul des outputs
dataset['Close_target'] = dataset.Close - dataset.Close.diff(-1)
#dataset['Returns'] = np.log(dataset['Close'] / dataset['Close'].shift(1))
#dataset['Returns_target'] = dataset.Returns - dataset.Returns.diff(-1)

# Boucle pour calculer les indicateurs avec différentes fenêtres
for window in range(30, 121, 30):
    dataset[f'cmf_{window}'] = tech.cmf(high=dataset.High, low=dataset.Low, close=dataset.Close, volume=dataset.Volume, window=window)
    dataset[f'rsi_{window}'] = tech.rsi(close=dataset.Close, window=window)
    dataset[f'ma_{window}'] = tech.ma(close=dataset.Close, window=window)
    dataset[f'ema_{window}'] = tech.ema(close=dataset.Close, window=window)
    dataset[f'atr_{window}'] = tech.atr(high=dataset.High, low=dataset.Low, close=dataset.Close, window=window)
    dataset[f'bollinger_{window}'] = tech.bollinger_band_width(close=dataset.Close, window=window, num_std=2)
dataset['obv'] = tech.obv(dataset.Close, dataset.Volume)

dataset = dataset.dropna()

In [4]:
dataset.describe()

Open           High            Low          Close  \
count  308160.000000  308160.000000  308160.000000  308160.000000   
mean    73094.566563   73121.067976   73067.911905   73094.664479   
std     15949.433994   15956.186130   15942.666718   15949.484839   
min     49351.260000   49817.200000   49000.000000   49338.490000   
25%     60832.010000   60851.737500   60812.000000   60832.010000   
50%     65763.255000   65778.010000   65748.000000   65763.250000   
75%     92997.122500   93050.000000   92939.497500   92997.952500   
max    108258.380000  108353.000000  108168.000000  108258.390000   

              Volume  Quote Asset Volume  Number of Trades  \
count  308160.000000        3.081600e+05     308160.000000   
mean       20.877350        1.551375e+06       2506.023627   
std        35.300633        2.687694e+06       2974.680077   
min         0.078720        5.071142e+03         58.000000   
25%         5.368910        3.710370e+05        720.000000   
50%        11.024305        7.855006e+05       1485.000000   
75%        22.950382        1.699828e+06       3138.000000   
max      2772.455670        2.598501e+08     149713.000000   

       Taker Buy Base Asset Volume  Taker Buy Quote Asset Volume  \
count                308160.000000                  3.081600e+05   
mean                     10.257933                  7.629806e+05   
std                      18.987742                  1.466875e+06   
min                       0.019860                  1.194658e+03   
25%                       2.050075                  1.420668e+05   
50%                       4.898835                  3.501994e+05   
75%                      11.191295                  8.261263e+05   
max                    1000.870788                  9.010270e+07   

        Close_target  ...         ema_90         atr_90   bollinger_90  \
count  308160.000000  ...  308160.000000  308160.000000  308160.000000   
mean    73094.763557  ...   73090.255667      53.160123     614.959828   
std     15949.536021  ...   15945.319626      38.140224     528.281879   
min     49338.490000  ...   50396.154191       1.178140       0.000000   
25%     60832.010000  ...   60830.233488      27.390643     295.628453   
50%     65763.250000  ...   65765.075735      43.105014     458.240699   
75%     92999.815000  ...   93063.618131      68.151390     740.251038   
max    108258.390000  ...  107645.849131     440.892178    7344.915597   

             cmf_120        rsi_120         ma_120        ema_120  \
count  308160.000000  308160.000000  308160.000000  308160.000000   
mean        0.005797      50.248892   73063.241628   73088.770217   
std         0.103409       5.394306   16008.696648   15943.937561   
min        -0.567805       0.000000       0.000000   50543.965839   
25%        -0.063235      46.520292   60827.881604   60825.398862   
50%         0.004186      50.255147   65766.748625   65768.259255   
75%         0.073039      53.898071   93076.093583   93085.004096   
max         0.548872      79.140046  107533.097250  107566.289584   

             atr_120  bollinger_120            obv  
count  308160.000000  308160.000000  308160.000000  
mean       53.159692     707.961667  -48307.942641  
std        37.222652     605.244217   20672.987954  
min         1.490087       0.000000  -83197.900310  
25%        27.805301     341.177537  -68438.715165  
50%        43.669367     525.971511  -45725.581949  
75%        68.079801     847.401764  -32683.182817  
max       383.452763    7844.286200     169.001120  

[8 rows x 35 columns]

In [ ]:
from gru_lib import GRUModel, Pipeline
%load_ext autoreload
%autoreload 2

# Définir les plages de valeurs pour les hyperparamètres
param_grid = {
    "period_size"   : [100000],
    "hidden_size"   : [8],
    "num_layers"    : [1],
    "dropout"       : [0.0],
    "lr"            : [0.1],
    "batch_size"    : [256*2],
    "epochs"        : [5],
    "num_workers"   : [4],
    "train_size"    : [0.7],
    "val_size"      : [0.15],
    "test_size"     : [0.15],
    "seq_size"      : [30]
}

inputs = [
    'Open', 'Close', 'High', 'Low', 
    'Volume', 'Number of Trades', 'Taker Buy Base Asset Volume',
    'obv', 'cmf_30', 'ema_30', 'atr_30',
    'rsi_30', 'ma_30', 'bollinger_30',
]
min_imputs = 6
outputs = 'Close_target'

result_path = os.getcwd()+f'\\train_result\\GRU-{ticker}-{interval}.csv'

# Générer toutes les combinaisons possibles d'hyperparamètres
param_combinations = list(itertools.product(*param_grid.values()))

# Générer toutes les combinaisons additives possibles des inputs
input_combinations = [list(itertools.combinations(inputs, r)) for r in range(min_imputs, len(inputs) + 1)]
input_combinations = [item for sublist in input_combinations for item in sublist]

counter = 0
for params, input_subset in itertools.product(param_combinations, input_combinations):
    time_lauch = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
    print(f'---------- Launch Time: {time_lauch:<10} ---------- Progress: {(counter):,}/{(len(param_combinations) * len(input_combinations)):,} ----------')

    # Extraire les paramètres pour cette combinaison
    hyperparams = dict(zip(param_grid.keys(), params))

    # Garder la période étudiée
    df = dataset.iloc[-hyperparams["period_size"]:]
    df = df.dropna()

    # Initialiser le modèle
    model = GRUModel(
        input_size=len(input_subset),
        output_size=1,
        hidden_size=hyperparams["hidden_size"], 
        num_layers=hyperparams["num_layers"],
        dropout=hyperparams["dropout"]
    )

    # Initialiser le pipeline
    pipeline = Pipeline(
        model=model, 
        dataset=df,
        inputs=list(input_subset),
        outputs=outputs
    )

    # Définir les hyperparamètres
    pipeline.hyper_param(
        lr=hyperparams["lr"], 
        batch_size=hyperparams["batch_size"], 
        epochs=hyperparams["epochs"],
        num_workers=hyperparams["num_workers"]
    )

    # Prétraitement des données
    pipeline.preprocess(
        train_size=hyperparams["train_size"],
        val_size=hyperparams["val_size"], 
        test_size=hyperparams["test_size"], 
        seq_size=hyperparams["seq_size"]
    )

    pipeline.train()
    pipeline.eval()
    pipeline.save(result_path)

    print("\n")
    counter += 1


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
---------- Launch Time: 2025-01-21 14:32:38 ---------- Progress: 0/12,911 ----------
Epoch 1/5, Train Loss: 9,051,078,596.204380, Validation Loss: 41,333,258,922.666664, Time: 0:00:00.903062
Epoch 2/5, Train Loss: 9,035,251,061.722628, Validation Loss: 41,260,979,848.533333, Time: 0:00:00.725753
Epoch 3/5, Train Loss: 9,019,826,452.554745, Validation Loss: 41,190,540,800.000000, Time: 0:00:00.731308
Epoch 4/5, Train Loss: 9,004,257,848.058393, Validation Loss: 41,119,444,172.800003, Time: 0:00:00.703619
Epoch 5/5, Train Loss: 8,988,640,540.029198, Validation Loss: 41,048,125,132.800003, Time: 0:00:00.710788
Time elapsed: 3.7745
Train Loss: 8,988,640,540.029198
Val Loss: 41,048,125,132.800003
Test Loss: 269,326,733,312.000000
R^2 : -223.6927
R^2 ajusté : -224.1432
MAPE : 0.9957
RMSE : 94,757.649161


---------- Launch Time: 2025-01-21 14:32:43 ---------- Progress: 1/12,911 ----------
Epoch 1/5, Train